In [7]:
import os
import pickle
import random
import time

import PIL
import numpy as np
import pandas as pd
import tensorflow as tf
from PIL import Image
from keras import Input, Model
from keras import backend as K
from keras.callbacks import TensorBoard
from keras.layers import Dense, LeakyReLU, BatchNormalization, ReLU, Reshape, UpSampling2D, Conv2D, Activation, \
    concatenate, Flatten, Lambda, Concatenate
from keras.optimizers import Adam
from matplotlib import pyplot as plt

import tensorflow as tf

def load_class_ids(class_info_file_path):
    """
    Load class ids from class_info.pickle file
    """
    with open(class_info_file_path, 'rb') as f:
        class_ids = pickle.load(f, encoding='latin1')
        return class_ids


def load_embeddings(embeddings_file_path):
    """
    훈련된 텍스트 임베딩을 불러옴
    """
    with open(embeddings_file_path, 'rb') as f:
        embeddings = pickle.load(f, encoding='latin1')
        embeddings = np.array(embeddings)
        print('embeddings: ', embeddings.shape)
    return embeddings


def load_filenames(filenames_file_path):
    """
    Load filenames.pickle file and return a list of all file names
    """
    with open(filenames_file_path, 'rb') as f:
        filenames = pickle.load(f, encoding='latin1')
    return filenames


def load_bounding_boxes(dataset_dir):
    """
    이미지와 그에 상응하는 바운딩 박스를 짝지어 딕셔너리로 만들어 출력
    """
    # 바운딩 박스 전체 경로
    bounding_boxes_path = os.path.join(dataset_dir, 'bounding_boxes.txt')
    file_paths_path = os.path.join(dataset_dir, 'images.txt')

    # bounding_boxes.txt 와 images.txt 파일을 읽어옴
    df_bounding_boxes = pd.read_csv(bounding_boxes_path,
                                    delim_whitespace=True, header=None).astype(int)
    df_file_names = pd.read_csv(file_paths_path, delim_whitespace=True, header=None)

    # 전체 이미지 파일 명이 순서대로 적힌 리스트를 만듬
    file_names = df_file_names[1].tolist()

    # 파일 이름에 대응하는 바운딩 박스가 들어갈 딕셔너리를 만듬 (딕셔너리는 크기를 임의로 증가시킬수 있으므로 초기 사이즈는 아무렇게나)
    filename_boundingbox_dict = {img_file[:-4]: [] for img_file in file_names[:2]}

    # 이미지 파일과 그에 해당하는 바운딩 박스를 딕셔너리로 만듬 (key = 이미지 파일 이름)
    for i in range(0, len(file_names)):
        # Get the bounding box
        bounding_box = df_bounding_boxes.iloc[i][1:].tolist()
        key = file_names[i][:-4]
        filename_boundingbox_dict[key] = bounding_box

    return filename_boundingbox_dict

'''
새 이미지가 크롭핑 되어있지 않기 크롭하기 위한 바운딩 박스 좌표 값이 파일에 주어지며,
그 파일을 토대로 이미지를 크로핑 한 후,
크로핑된 모든 이미지를 지정한 이미지 크기 (image_size) 값으로 바꾼다
'''
def get_img(img_path, bbox, image_size):
    """
    Load and resize image
    """
    img = Image.open(img_path).convert('RGB')
    width, height = img.size
    if bbox is not None:
        R = int(np.maximum(bbox[2], bbox[3]) * 0.75)
        center_x = int((2 * bbox[0] + bbox[2]) / 2)
        center_y = int((2 * bbox[1] + bbox[3]) / 2)
        y1 = np.maximum(0, center_y - R)
        y2 = np.minimum(height, center_y + R)
        x1 = np.maximum(0, center_x - R)
        x2 = np.minimum(width, center_x + R)
        img = img.crop([x1, y1, x2, y2])
    img = img.resize(image_size, PIL.Image.BILINEAR)
    return img


def load_dataset(filenames_file_path, class_info_file_path, cub_dataset_dir, embeddings_file_path, image_size):
    """
    Load dataset
    """
    filenames = load_filenames(filenames_file_path)
    class_ids = load_class_ids(class_info_file_path)
    bounding_boxes = load_bounding_boxes(cub_dataset_dir)
    all_embeddings = load_embeddings(embeddings_file_path)

    X, y, embeddings = [], [], []

    print("Embeddings shape:", all_embeddings.shape)
    
    # 각 이미지에 해당하는 바운딩 박스를 추출하여 get_img 함수로 크로핑되고 같은 크기로 바뀐 이미지를 
    for index, filename in enumerate(filenames):
        bounding_box = bounding_boxes[filename]

        try:
            # Load images
            img_name = '{}/images/{}.jpg'.format(cub_dataset_dir, filename)
            img = get_img(img_name, bounding_box, image_size)

            all_embeddings1 = all_embeddings[index, :, :]

            embedding_ix = random.randint(0, all_embeddings1.shape[0] - 1)
            embedding = all_embeddings1[embedding_ix, :]
            # X = 정제한 이미지 리스트
            X.append(np.array(img))
            # y = 정제한 이미지 인덱스
            y.append(class_ids[index])
            # embeddings = 
            embeddings.append(embedding)
        except Exception as e:
            print(e)

    X = np.array(X)
    y = np.array(y)
    embeddings = np.array(embeddings)
    return X, y, embeddings


def generate_c(x):
    mean = x[:, :128]
    log_sigma = x[:, 128:]
    stddev = K.exp(log_sigma)
    epsilon = K.random_normal(shape=K.constant((mean.shape[1],), dtype='int32'))
    c = stddev * epsilon + mean
    return c


def build_ca_model():
    """
    (1024,)의 텍스트 인코더 신경망의 출력을 입력으로 받고 (256,) 의 텐서를 출력
    """
    input_layer = Input(shape=(1024,))
    x = Dense(256)(input_layer)
    x = LeakyReLU(alpha=0.2)(x)
    model = Model(inputs=[input_layer], outputs=[x])
    return model


def build_embedding_compressor_model():
    """
    Build embedding compressor model
    """
    input_layer = Input(shape=(1024,))
    x = Dense(128)(input_layer)
    x = ReLU()(x)

    model = Model(inputs=[input_layer], outputs=[x])
    return model


def build_stage1_generator():
    """
    Stage-I 의 generator 
    *** 이 신경망 안에 CA 신경망과 생성기 신경망이 들어가 있다!!!! ***
    그러므로, 입력으로 텍스트 임베딩 출력 (1024,)과 잡음 변수(100,) 을 받는다
    """
    input_layer = Input(shape=(1024,))
    x = Dense(256)(input_layer)
    mean_logsigma = LeakyReLU(alpha=0.2)(x)

    c = Lambda(generate_c)(mean_logsigma)

    input_layer2 = Input(shape=(100,))
    '''
    텍스트 조건부 변수를 잡음 변수와 접합(concatenation) -> cGAN
    '''
    gen_input = Concatenate(axis=1)([c, input_layer2])

    x = Dense(128 * 8 * 4 * 4, use_bias=False)(gen_input)
    x = ReLU()(x)

    x = Reshape((4, 4, 128 * 8), input_shape=(128 * 8 * 4 * 4,))(x)

    x = UpSampling2D(size=(2, 2))(x)
    x = Conv2D(512, kernel_size=3, padding="same", strides=1, use_bias=False)(x)
    x = BatchNormalization()(x)
    x = ReLU()(x)

    x = UpSampling2D(size=(2, 2))(x)
    x = Conv2D(256, kernel_size=3, padding="same", strides=1, use_bias=False)(x)
    x = BatchNormalization()(x)
    x = ReLU()(x)

    x = UpSampling2D(size=(2, 2))(x)
    x = Conv2D(128, kernel_size=3, padding="same", strides=1, use_bias=False)(x)
    x = BatchNormalization()(x)
    x = ReLU()(x)

    x = UpSampling2D(size=(2, 2))(x)
    x = Conv2D(64, kernel_size=3, padding="same", strides=1, use_bias=False)(x)
    x = BatchNormalization()(x)
    x = ReLU()(x)

    x = Conv2D(3, kernel_size=3, padding="same", strides=1, use_bias=False)(x)
    x = Activation(activation='tanh')(x)
    
    stage1_gen = Model(inputs=[input_layer, input_layer2], outputs=[x, mean_logsigma])
    '''
    stage - I gen 은 입력된 문장의 임베딩을 바탕으로 (+잡음 변수) 이미지를 생성 함 
    '''
    return stage1_gen


def build_stage1_discriminator():
    """
    Create a model which takes two inputs
    1. One from above network
    2. One from the embedding layer
    3. Concatenate along the axis dimension and feed it to the last module which produces final logits
    """
    input_layer = Input(shape=(64, 64, 3))

    x = Conv2D(64, (4, 4),
               padding='same', strides=2,
               input_shape=(64, 64, 3), use_bias=False)(input_layer)
    x = LeakyReLU(alpha=0.2)(x)

    x = Conv2D(128, (4, 4), padding='same', strides=2, use_bias=False)(x)
    x = BatchNormalization()(x)
    x = LeakyReLU(alpha=0.2)(x)

    x = Conv2D(256, (4, 4), padding='same', strides=2, use_bias=False)(x)
    x = BatchNormalization()(x)
    x = LeakyReLU(alpha=0.2)(x)

    x = Conv2D(512, (4, 4), padding='same', strides=2, use_bias=False)(x)
    x = BatchNormalization()(x)
    x = LeakyReLU(alpha=0.2)(x)
    
    '''
    실제 이미지에 해당하는 압축된 임베딩을 입력
    '''
    input_layer2 = Input(shape=(4, 4, 128))
    
    '''
    입력 이미지와 압축 텍스트 임베딩을 합침
    '''
    merged_input = concatenate([x, input_layer2])

    x2 = Conv2D(64 * 8, kernel_size=1,
                padding="same", strides=1)(merged_input)
    x2 = BatchNormalization()(x2)
    x2 = LeakyReLU(alpha=0.2)(x2)
    x2 = Flatten()(x2)
    x2 = Dense(1)(x2)
    x2 = Activation('sigmoid')(x2)

    stage1_dis = Model(inputs=[input_layer, input_layer2], outputs=[x2])
    '''
    출력은 입력 이미지가 진짜인지 가짜인지에 관한 확률(sigmoid)을 출력
    '''
    return stage1_dis


def build_adversarial_model(gen_model, dis_model):
    input_layer = Input(shape=(1024,))
    input_layer2 = Input(shape=(100,))
    input_layer3 = Input(shape=(4, 4, 128))

    x, mean_logsigma = gen_model([input_layer, input_layer2])

    dis_model.trainable = False
    valid = dis_model([x, input_layer3])

    model = Model(inputs=[input_layer, input_layer2, input_layer3], outputs=[valid, mean_logsigma])
    return model


def KL_loss(y_true, y_pred):
    mean = y_pred[:, :128]
    logsigma = y_pred[:, :128]
    loss = -logsigma + .5 * (-1 + K.exp(2. * logsigma) + K.square(mean))
    loss = K.mean(loss)
    return loss


def custom_generator_loss(y_true, y_pred):
    # Calculate binary cross entropy loss
    return K.binary_crossentropy(y_true, y_pred)

'''
def save_rgb_img(img, path):
    """
    Save an rgb image
    """
    fig = plt.figure()
    ax = fig.add_subplot(1, 1, 1)
    ax.imshow(img)
    ax.axis("off")
    ax.set_title("Image")

    plt.savefig(path)
    plt.close()
'''
def save_rgb_img(img_gen, img_real, path):
    """
    Save an rgb image
    """
    fig = plt.figure()
    ax = fig.add_subplot(1, 2, 1)
    ax.imshow(img_gen)
    ax.axis("off")
    ax.set_title("Image_gen")
    
    ax = fig.add_subplot(1, 2, 2)
    ax.imshow(img_real)
    ax.axis("off")
    ax.set_title("Image_real")
    
    plt.savefig(path)
    plt.close()


def write_log(callback, name, loss, batch_no):
    """
    Write training summary to TensorBoard
    """
    with callback.as_default():
          tf.summary.scalar(name, loss, batch_no)
          callback.flush()
    
    
    
    
    
    
'''
Stage - I stackGAN 훈련
'''
if __name__ == '__main__':
    '''
    하이퍼파라미터(불변 파라미터) 지정
    '''
    data_dir = "/home/csle/Desktop/CUB"
    train_dir = data_dir + "/train"
    test_dir = data_dir + "/test"
    image_size = 64
    batch_size = 64
    z_dim = 100
    stage1_generator_lr = 0.0002
    stage1_discriminator_lr = 0.0002
    stage1_lr_decay_step = 600
    epochs = 1000
    condition_dim = 128

    embeddings_file_path_train = train_dir + "/char-CNN-RNN-embeddings.pickle"
    embeddings_file_path_test = test_dir + "/char-CNN-RNN-embeddings.pickle"

    filenames_file_path_train = train_dir + "/filenames.pickle"
    filenames_file_path_test = test_dir + "/filenames.pickle"

    class_info_file_path_train = train_dir + "/class_info.pickle"
    class_info_file_path_test = test_dir + "/class_info.pickle"

    cub_dataset_dir = data_dir + "/CUB_200_2011"
    
    '''
    optimizer 정의
    '''
    dis_optimizer = Adam(lr=stage1_discriminator_lr, beta_1=0.5, beta_2=0.999)
    gen_optimizer = Adam(lr=stage1_generator_lr, beta_1=0.5, beta_2=0.999)

    """"
    dataset 로드하기
    """
    X_train, y_train, embeddings_train = load_dataset(filenames_file_path=filenames_file_path_train,
                                                      class_info_file_path=class_info_file_path_train,
                                                      cub_dataset_dir=cub_dataset_dir,
                                                      embeddings_file_path=embeddings_file_path_train,
                                                      image_size=(64, 64))

    X_test, y_test, embeddings_test = load_dataset(filenames_file_path=filenames_file_path_test,
                                                   class_info_file_path=class_info_file_path_test,
                                                   cub_dataset_dir=cub_dataset_dir,
                                                   embeddings_file_path=embeddings_file_path_test,
                                                   image_size=(64, 64))

print('finish')

embeddings:  (8855, 10, 1024)
Embeddings shape: (8855, 10, 1024)
embeddings:  (2933, 10, 1024)
Embeddings shape: (2933, 10, 1024)
finish


In [8]:
import tensorflow as tf 

config = tf.compat.v1.ConfigProto() 
config.gpu_options.per_process_gpu_memory_fraction = 0.6 
session = tf.compat.v1.Session(config=config)



"""
신경망 빌드 & compile
"""
ca_model = build_ca_model()
ca_model.compile(loss="binary_crossentropy", optimizer="adam")

stage1_dis = build_stage1_discriminator()
stage1_dis.compile(loss='binary_crossentropy', optimizer=dis_optimizer)

stage1_gen = build_stage1_generator()
stage1_gen.compile(loss="mse", optimizer=gen_optimizer)

embedding_compressor_model = build_embedding_compressor_model()
embedding_compressor_model.compile(loss="binary_crossentropy", optimizer="adam")

'''
stage-I GAN 빌드& 컴파일
이때, stage-I 의 discriminator 는 훈련시키지 않고 stage-I generator 의 가중치만 업데이트
'''
adversarial_model = build_adversarial_model(gen_model=stage1_gen, dis_model=stage1_dis)
adversarial_model.compile(loss=['binary_crossentropy', KL_loss], loss_weights=[1, 2.0],
                          optimizer=gen_optimizer, metrics=None)

'''
tensorboard = TensorBoard(log_dir="logs/".format(time.time()))
tensorboard.set_model(stage1_gen)
tensorboard.set_model(stage1_dis)
tensorboard.set_model(ca_model)
tensorboard.set_model(embedding_compressor_model)
'''

# Generate an array containing real and fake values
# Apply label smoothing as well
real_labels = np.ones((batch_size, 1), dtype=float) * 0.9
fake_labels = np.zeros((batch_size, 1), dtype=float) * 0.1
'''
매 epoch 마다 아래를 반복함
'''
for epoch in range(epochs):
    print("========================================")
    print("Epoch is:", epoch)
    print("Number of batches", int(X_train.shape[0] / batch_size))

    gen_losses = []
    dis_losses = []

    # Load data and train model
    number_of_batches = int(X_train.shape[0] / batch_size)
    for index in range(number_of_batches):
        print("Batch:{}".format(index+1))
        '''
        모델에 입력으로 들어갈 이미지와 텍스트 임베딩을 받아옴 (각 텍스트 임베딩은 각 이미지에 대응 됨)
        '''
        # 원래는 CA 의 출력이 stage-I 으로 들어가야 하지만 gen 안에 CA 가 있음
        z_noise = np.random.normal(0, 1, size=(batch_size, z_dim))
        # 배치 사이즈만큼 훈련(실제) 이미지를 추출
        image_batch = X_train[index * batch_size:(index + 1) * batch_size]
        # 추출한 이미지에 대응하는 임베딩을 추출
        embedding_batch = embeddings_train[index * batch_size:(index + 1) * batch_size]
        # 이미지들을 정규화하여 값을 작게 만듬
        image_batch = (image_batch - 127.5) / 127.5

        # stage-I 의 gen 에서 텍스트 임베딩을 바탕으로 저 해상도 fake 이미지를 생성
        # 이때, 두 stage 는 랜덤하게 생성한 텍스트 임베딩을 나머지 입력으로 받음
        fake_images, _ = stage1_gen.predict([embedding_batch, z_noise], verbose=3)

        # stage-I dis 에 들어갈 압축 텍스트 임베딩을 랜덤하게 생성한 텍스트 임베딩 기반으로 생성
        compressed_embedding = embedding_compressor_model.predict_on_batch(embedding_batch)
        compressed_embedding = np.reshape(compressed_embedding, (-1, 1, 1, condition_dim))
        compressed_embedding = np.tile(compressed_embedding, (1, 4, 4, 1))
        """
        stage-I dis 를 훈련함
        """
        # 실제 이미지와 압축 텍스트 임베딩을 입력으로 하고 모든 레이블을 1 (이미지가 진짜라는 의미) 로 하여,
        # dis 가 실제 이미지를 잘 분류 하게끔 훈련
        dis_loss_real = stage1_dis.train_on_batch([image_batch, compressed_embedding],
                                                  np.reshape(real_labels, (batch_size, 1)))
        # gen 이 생성한 가짜 이미지와 압축 텍스트 임베딩을 입력으로 하고 모든 레이블을 0 (이미지가 가짜라는 의미) 로 하여,
        # dis 가 가짜 이미지를 잘 분류 하게끔 훈련
        dis_loss_fake = stage1_dis.train_on_batch([fake_images, compressed_embedding],
                                                  np.reshape(fake_labels, (batch_size, 1)))
        # 실제 이미지와 압축 텍스트 임베딩을 '어긋나게' 입력으로 하고 모든 레이블을 0 (이미지가 가짜라는 의미) 로 하여,
        # dis 가 실제 이미지를 잘 분류 하게끔 훈련
        dis_loss_wrong = stage1_dis.train_on_batch([image_batch[:(batch_size - 1)], compressed_embedding[1:]],
                                                   np.reshape(fake_labels[1:], (batch_size-1, 1)))

        d_loss = 0.5 * np.add(dis_loss_real, 0.5 * np.add(dis_loss_wrong, dis_loss_fake))

        print("d_loss_real:{}".format(dis_loss_real))
        print("d_loss_fake:{}".format(dis_loss_fake))
        print("d_loss_wrong:{}".format(dis_loss_wrong))
        print("d_loss:{}".format(d_loss))

        """
        stage-I GAN 을 훈련함
        이때, stage-I 의 discriminator 는 훈련시키지 않고 stage-I generator 의 가중치만 업데이트
        """
        g_loss = adversarial_model.train_on_batch([embedding_batch, z_noise, compressed_embedding],[K.ones((batch_size, 1)) * 0.9, K.ones((batch_size, 256)) * 0.9])
        print("g_loss:{}".format(g_loss))

        dis_losses.append(d_loss)
        gen_losses.append(g_loss)

    """
    각 epoch 마다 Tensorboard 에 loss 저장
    """
    writer = tf.summary.create_file_writer("logs/".format(time.time()))
    write_log(writer, 'discriminator_loss', np.mean(dis_losses), epoch)
    write_log(writer, 'generator_loss', np.mean(gen_losses[0]), epoch)

    # 매 두번의 epoch 마다 이미지 gen & 이미지 저장
    if epoch % 2 == 0:
        # z_noise2 = np.random.uniform(-1, 1, size=(batch_size, z_dim))
        z_noise2 = np.random.normal(0, 1, size=(batch_size, z_dim))
        embedding_batch = embeddings_test[0:batch_size]
        fake_images, _ = stage1_gen.predict_on_batch([embedding_batch, z_noise2])

        # Save images
        '''
        for i, img in enumerate(fake_images[:10]):
            save_rgb_img(img, "results/gen_{}_{}.png".format(epoch, i))
        '''
        for i in range(5):
            img_gen = fake_images[i]
            img_real = X_test[i]
            save_rgb_img(img_gen, img_real, "results/gen_{}_{}.png".format(epoch, i))

    if epoch % 50 == 0:
        # Save models
        stage1_gen.save_weights("weights/stage1_gen_epoch_{}.h5".format(epoch))
        stage1_dis.save_weights("weights/stage1_dis_epoch_{}.h5".format(epoch))

'''
이제 훈련된 stage-I 의 generator 와 discriminator 을 얻음 (+ embedding_compressor) 
'''

Epoch is: 0
Number of batches 138
Batch:1
d_loss_real:0.8286257982254028
d_loss_fake:3.775149345397949
d_loss_wrong:5.526351451873779
d_loss:2.7396880984306335
g_loss:[0.7055438756942749, 0.6752235889434814, 0.015160144306719303]
Batch:2
d_loss_real:0.8516981601715088
d_loss_fake:0.847032368183136
d_loss_wrong:0.7663309574127197
d_loss:0.8291899114847183
g_loss:[0.7302665710449219, 0.7043249011039734, 0.012970846146345139]
Batch:3
d_loss_real:2.9087493419647217
d_loss_fake:1.0124927759170532
d_loss_wrong:0.7796817421913147
d_loss:1.9024183005094528
g_loss:[0.7283855676651001, 0.6962435245513916, 0.0160710196942091]
Batch:4
d_loss_real:3.7603232860565186
d_loss_fake:0.035865239799022675
d_loss_wrong:1.797307014465332
d_loss:2.338454706594348
g_loss:[0.7122957706451416, 0.6849417090415955, 0.013677025213837624]
Batch:5
d_loss_real:2.379462242126465
d_loss_fake:0.4004283547401428
d_loss_wrong:2.0508785247802734
d_loss:1.8025578409433365
g_loss:[0.7448036074638367, 0.7232956290245056, 0.01

d_loss_real:1.1547958850860596
d_loss_fake:0.007415242027491331
d_loss_wrong:0.7234342098236084
d_loss:0.7601103055058047
g_loss:[0.6825087666511536, 0.6761531233787537, 0.0031778316479176283]
Batch:43
d_loss_real:1.0099413394927979
d_loss_fake:0.0014677077997475863
d_loss_wrong:0.729417085647583
d_loss:0.6876918681082316
g_loss:[0.6853940486907959, 0.6790900230407715, 0.0031520144548267126]
Batch:44
d_loss_real:0.9384925365447998
d_loss_fake:0.0046426947228610516
d_loss_wrong:0.7864570021629333
d_loss:0.6670211924938485
g_loss:[0.6393943428993225, 0.6333646774291992, 0.003014837158843875]
Batch:45
d_loss_real:1.0515393018722534
d_loss_fake:0.022799326106905937
d_loss_wrong:0.6606748104095459
d_loss:0.6966381850652397
g_loss:[0.6654011011123657, 0.6582002639770508, 0.0036004241555929184]
Batch:46
d_loss_real:0.9389156103134155
d_loss_fake:0.002085575135424733
d_loss_wrong:0.7798402309417725
d_loss:0.6649392566760071
g_loss:[0.6214090585708618, 0.6150505542755127, 0.003179264720529318]


d_loss_real:0.844434380531311
d_loss_fake:0.0005753949517384171
d_loss_wrong:0.7209215760231018
d_loss:0.6025914330093656
g_loss:[0.3982187807559967, 0.3934019207954407, 0.002408432774245739]
Batch:84
d_loss_real:0.8915146589279175
d_loss_fake:0.0009898246498778462
d_loss_wrong:0.7302019596099854
d_loss:0.6285552755289245
g_loss:[0.4018312692642212, 0.39613059163093567, 0.002850334160029888]
Batch:85
d_loss_real:0.8909833431243896
d_loss_fake:0.00038719200529158115
d_loss_wrong:0.7216385006904602
d_loss:0.6259980947361328
g_loss:[0.34915098547935486, 0.34284883737564087, 0.0031510749831795692]
Batch:86
d_loss_real:0.8948101997375488
d_loss_fake:0.000659138080663979
d_loss_wrong:0.698750913143158
d_loss:0.6222576126747299
g_loss:[0.3575398027896881, 0.3516601324081421, 0.002939831465482712]
Batch:87
d_loss_real:0.8955262303352356
d_loss_fake:0.0007267908076755702
d_loss_wrong:0.696815013885498
d_loss:0.6221485663409112
g_loss:[0.36375197768211365, 0.35749077796936035, 0.0031306028831750

g_loss:[0.344253808259964, 0.3380717635154724, 0.0030910216737538576]
Batch:124
d_loss_real:0.9296355247497559
d_loss_fake:0.0005283909849822521
d_loss_wrong:0.6678043007850647
d_loss:0.6319009353173897
g_loss:[0.3502841293811798, 0.3444460332393646, 0.002919054590165615]
Batch:125
d_loss_real:0.8417490720748901
d_loss_fake:0.0010981468949466944
d_loss_wrong:0.7047542333602905
d_loss:0.5973376311012544
g_loss:[0.35291463136672974, 0.34686654806137085, 0.0030240463092923164]
Batch:126
d_loss_real:0.8756192922592163
d_loss_fake:0.00035646010655909777
d_loss_wrong:0.6872788667678833
d_loss:0.6097184778482188
g_loss:[0.3614005744457245, 0.3560310900211334, 0.0026847366243600845]
Batch:127
d_loss_real:0.9495490789413452
d_loss_fake:0.002615931211039424
d_loss_wrong:0.6772875785827637
d_loss:0.6447504169191234
g_loss:[0.33165040612220764, 0.32591700553894043, 0.0028666933067142963]
Batch:128
d_loss_real:0.8647783398628235
d_loss_fake:0.0013482574140653014
d_loss_wrong:0.7729019522666931
d_lo

Clipping input data to the valid range for imshow with RGB data ([0..1] for floats or [0..255] for integers).
Clipping input data to the valid range for imshow with RGB data ([0..1] for floats or [0..255] for integers).
Clipping input data to the valid range for imshow with RGB data ([0..1] for floats or [0..255] for integers).
Clipping input data to the valid range for imshow with RGB data ([0..1] for floats or [0..255] for integers).
Clipping input data to the valid range for imshow with RGB data ([0..1] for floats or [0..255] for integers).


...

g_loss:[0.34329953789711, 0.34312281012535095, 8.836798224365339e-05]
Batch:81
d_loss_real:0.350826233625412
d_loss_fake:4.980701305612456e-06
d_loss_wrong:0.00856032408773899
d_loss:0.17755444300996714
g_loss:[0.34098994731903076, 0.3408511281013489, 6.941390893189237e-05]
Batch:82
d_loss_real:0.3533014953136444
d_loss_fake:2.992208919749828e-06
d_loss_wrong:0.006607110146433115
d_loss:0.17830327324566042
g_loss:[0.33597415685653687, 0.33582115173339844, 7.64995493227616e-05]
Batch:83
d_loss_real:0.34383007884025574
d_loss_fake:2.103618044202449e-06
d_loss_wrong:0.0043022180907428265
d_loss:0.17299111984732463
g_loss:[0.3285156488418579, 0.3283233642578125, 9.6138144726865e-05]
Batch:84
d_loss_real:0.3385809659957886
d_loss_fake:3.775360710278619e-06
d_loss_wrong:0.006295311264693737
d_loss:0.1708652546542453
g_loss:[0.32742178440093994, 0.3272084593772888, 0.00010665931040421128]
Batch:85
d_loss_real:0.35321861505508423
d_loss_fake:4.8369083742727526e-06
d_loss_wrong:0.01097486820071

g_loss:[0.33138948678970337, 0.33041688799858093, 0.00048630143282935023]
Batch:121
d_loss_real:0.3430832028388977
d_loss_fake:2.8030701741954545e-06
d_loss_wrong:0.004461691714823246
d_loss:0.1726577251156982
g_loss:[0.3277811110019684, 0.3276061415672302, 8.748029358685017e-05]
Batch:122
d_loss_real:0.33928656578063965
d_loss_fake:2.6739076020021457e-06
d_loss_wrong:0.005385091062635183
d_loss:0.17099022413287912
g_loss:[0.3285221755504608, 0.32835906744003296, 8.155644900398329e-05]
Batch:123
d_loss_real:0.3656119704246521
d_loss_fake:2.2169485873746453e-06
d_loss_wrong:0.0025437138974666595
d_loss:0.18344246792383956
g_loss:[0.3285762369632721, 0.32840847969055176, 8.38723499327898e-05]
Batch:124
d_loss_real:0.38495469093322754
d_loss_fake:1.5669872936996398e-06
d_loss_wrong:0.011929726228117943
d_loss:0.19546016877046668
g_loss:[0.3376282751560211, 0.3375011682510376, 6.35510659776628e-05]
Batch:125
d_loss_real:0.33944594860076904
d_loss_fake:5.250763933872804e-06
d_loss_wrong:0.0

g_loss:[0.3271133005619049, 0.3269377648830414, 8.776919275987893e-05]
Batch:23
d_loss_real:0.3481738567352295
d_loss_fake:4.744060333905509e-06
d_loss_wrong:0.013275248929858208
d_loss:0.17740692661516277
g_loss:[0.32795974612236023, 0.3277896046638489, 8.507567690685391e-05]
Batch:24
d_loss_real:0.3388548493385315
d_loss_fake:5.117673936183564e-06
d_loss_wrong:0.0030509440694004297
d_loss:0.1701914401050999
g_loss:[0.3275189995765686, 0.32715505361557007, 0.0001819703757064417]
Batch:25
d_loss_real:0.348930686712265
d_loss_fake:8.347480616066605e-06
d_loss_wrong:0.008951405063271523
d_loss:0.1767052814921044
g_loss:[0.3292991518974304, 0.32909315824508667, 0.00010300187568645924]
Batch:26
d_loss_real:0.3431068956851959
d_loss_fake:4.10932807426434e-06
d_loss_wrong:0.008364208042621613
d_loss:0.17364552718527193
g_loss:[0.32768452167510986, 0.32750606536865234, 8.923390123527497e-05]
Batch:27
d_loss_real:0.34126511216163635
d_loss_fake:6.149298769742018e-06
d_loss_wrong:0.006030274555

d_loss_real:0.36691921949386597
d_loss_fake:1.753570541040972e-05
d_loss_wrong:0.007791771087795496
d_loss:0.18541193644523446
g_loss:[0.34810662269592285, 0.34773093461990356, 0.00018784563872031868]
Batch:64
d_loss_real:0.36214980483055115
d_loss_fake:1.5168265235843137e-05
d_loss_wrong:0.012632534839212894
d_loss:0.18423682819138776
g_loss:[0.3370344936847687, 0.33636730909347534, 0.0003335902583785355]
Batch:65
d_loss_real:0.34651002287864685
d_loss_fake:4.836473453906365e-05
d_loss_wrong:0.006811514962464571
d_loss:0.17496998136357433
g_loss:[0.3329218029975891, 0.3323092758655548, 0.00030626021907664835]
Batch:66
d_loss_real:0.3410397469997406
d_loss_fake:1.181082370749209e-05
d_loss_wrong:0.006670214701443911
d_loss:0.17219037988115815
g_loss:[0.3292894959449768, 0.32897400856018066, 0.00015773801715113223]
Batch:67
d_loss_real:0.3464561104774475
d_loss_fake:1.0909810043813195e-05
d_loss_wrong:0.007702046073973179
d_loss:0.175156294209728
g_loss:[0.3281862139701843, 0.3279067575

KeyboardInterrupt: 